# Fase 2
NOTA:
- In questa fase, le immagini da inserire nel database saranno etichettate come image-X-Y- Z.png, dove
    - X ∈ {cc, con, detail, emboss, jitter, neg, noise1, noise2, original, poster, rot, smooth, stipple} denota il tipo dell’immagine;
    - 1≤Y≤40denota ilsubjectID,and
    - 1 ≤ Z ≤ 10 denota l’ ID del campione dell’immagine.
    

- I task in questa fase riguardano i tre modelli di feature e le misure di distanza/similarita’ sviluppate nella precedente.
 
- Potete usare le librerie esistenti per la decomposizione LDA.
- Potete usare le librerie esistenti per l’estrazione di autovalori e autovettori.

# Task 1
Implementare un programma che , dati (a) uno dei tre modelli di feature, (b) un valore per X specificato dall’utente, (c) un valore “k” specificato dall’utente, (d) una delle 3 tecniche di riduzione della dimensionalita’ (PCA, SVD, LDA) scelta dall’utente, restituisca le top-k semantiche latenti estratte utilizzando immagini del tipo specificato.

> **Nota bene:** Ciascuna semantica latente deve essere presentata sotto forma di sequenza di coppie soggetto-peso, ordinate in modo decrescente rispetto ai pesi. Salvate le semantiche latenti in un file di output opportunamente etichettato (ossia, con nome informativo).

> **DA SISTEMARE:** ANCORA NON RESTITUIAMO LE TOP K


# Task 2
Implementare un programma che, dati (a) uno dei tre modelli di feature, (b) un valore per Y specificato dall’utente, (c) un valore “k” specificato dall’utente (d) ) una delle 3 tecniche di riduzione della dimensionalita’ (PCA, SVD, LDA) scelta dall’utente, restituisca le top-k semantiche latenti estratte utilizzando immagini del soggetto specificato.

> **Nota bene:** Ciascuna semantica latente deve essere presentata sotto forma di sequenza di coppie tipo- peso, ordinate in modo decrescente rispetto ai pesi. Salvate le semantiche latenti in un file di output opportunamente etichettato (ossia, con nome informativo).


In [44]:
from ipynb.fs.full.task1_new import *
import numpy as np
from operator import itemgetter

from PIL import Image
from numpy import asarray
from scipy.stats import skew

# load and display an image with Matplotlib
from matplotlib import image
from matplotlib import pyplot
import matplotlib.pyplot as plt

from sklearn.decomposition import PCA
from scipy.linalg import svd
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis

from sklearn.pipeline import Pipeline
from sklearn.naive_bayes import GaussianNB
import re
from sklearn.utils.extmath import randomized_svd
import json


In [4]:
# import OS module
import os

# Get the list of all files and directories
path = "./secondaparte/images/"
dir_list = os.listdir(path) # array di stringhe contenente i nomi dei file
 
dir_list.sort()
dir_list.remove('.DS_Store')

print(len(dir_list))

4787


In [73]:
def createDictionaryAndWriteOnFile(matrix, filtered_dir_list, passedParameter):
    matrixtrasposta = matrix.T

    dictionaryFeaturesLatenti = {}
    for i in range(len(matrixtrasposta)):
        sequenzaFeatureLatente = []
        for j in range(len(matrixtrasposta[i])):
            splittedString = re.split('-', filtered_dir_list[j])
            pair = ()

            if passedParameter == 'X':
                pair = (splittedString[2], matrixtrasposta[i][j])
            elif passedParameter == 'Y':
                pair = (splittedString[1], matrixtrasposta[i][j])
            
            sequenzaFeatureLatente.append(pair)
        
        sequenzaOrdinata = sorted(sequenzaFeatureLatente, key=lambda x: x[1], reverse=True)
        dictionaryFeaturesLatenti['Feature' + str(i)] = sequenzaOrdinata

    #print(dictionaryFeaturesLatenti)

    fileName = ''

    if passedParameter == 'X':
        fileName = 'coppie_soggetto-peso.txt'
    elif passedParameter == 'Y':
        fileName = 'coppie_tipo-peso.txt'

    # controlliamo se il file esiste o no
    file = open('./outputfilesecondaparte/' + fileName,'w+')

    with open('./outputfilesecondaparte/' + fileName, 'w') as convert_file:
        convert_file.write(json.dumps(dictionaryFeaturesLatenti, indent=4, sort_keys=True))

In [74]:
# funzione usata per ottenre le top-k semantiche latenti.
# parametri della funzione:
# modelName: nome del modello da usare (ColorMoments, LBP, HOG)
# X: il tipo dell'immagine
# k: numero delle semantiche da estrarre
# strategyName: nome della tecnica con cui su vuole effettuare la riduzione di dimensionalità (PCA, SVD, LDA)

def ottieniKSemanticheLatenti(modelName, param, k, strategyName, passedParameter):
    # apriamo l'immagine

    # imagePath = 'secondaparte/images/image-' + X + '-1-1.png'
    # image = Image.open(imagePath)

    # # convertiamo l'immagine in un numpy array
    # data = asarray(image)
    # print(data)

    # plt.imshow(image, cmap ="gray")
    # plt.show()

    filtered_dir_list = []

    if passedParameter == 'X':
        filtered_dir_list = list(filter(lambda k: param in k, dir_list))
    elif passedParameter == 'Y':
        for i in range(len(dir_list)):
            splittedString = re.split('-', dir_list[i])

            if splittedString[2] == param:
                filtered_dir_list.append(dir_list[i])

    print("Numero di file su cui applichiamo i metodi: ", len(filtered_dir_list))
    #print(filtered_dir_list)
    dictionaryOfDescriptors = {}

    match modelName:
        case 'ColorMoments':
            print("SONO IN COLOR MOMENTS")
            # salvataggio dei descrittori dei color moments

            for i in range(0, len(filtered_dir_list)):
                colorMomentsOfImage = ottieniDescrittoreSecondaParte(
                    filtered_dir_list[i], 'ColorMoments')
                dictionaryOfDescriptors[filtered_dir_list[i]
                                        ] = colorMomentsOfImage

        case 'LBP':
            print("SONO IN LBP")
            # salvataggio dei descrittori dei color moments

            for i in range(0, len(filtered_dir_list)):
                LBPofImages = ottieniDescrittoreSecondaParte(
                    filtered_dir_list[i], 'LBP')
                dictionaryOfDescriptors[filtered_dir_list[i]] = LBPofImages

        case 'HOG':
            print("HOG")
        case _:
            return 4

    matrixObjFeatures = []

    for key in dictionaryOfDescriptors:
        matrixObjFeatures.append(dictionaryOfDescriptors[key])

    print("Lunghezza di un descrittore: ", len(matrixObjFeatures[0]))

    match strategyName:
        case 'PCA':
            print("SONO IN PCA")

            numpyMatrixObjFeatures = np.array(matrixObjFeatures)

            covMatr = np.cov(numpyMatrixObjFeatures.T)

            print("\nNumero righe matrice di covarianza: ", len(covMatr))
            print("Numero colonne matrice di covarianza: ", len(covMatr[0]))
            print("La matrice di covarianza è quadrata? ", len(covMatr) == len(covMatr[0]))

            pca = PCA(n_components=k)
            converted_data = pca.fit_transform(matrixObjFeatures)
            print("\n")
            print(converted_data)

            print("\nNumero righe matrice di converted_data: ", len(converted_data))
            print("Numero colonne matrice di converted_data: ", len(converted_data[0]))

            # Questa imlementazione di PCA mi dà una matrice che ha tante righe quanti sono gli oggetti e tante colonne quante sono le features
            # mi descrive gli oggetti sulla base delle nuove features latenti

            createDictionaryAndWriteOnFile(converted_data, filtered_dir_list, passedParameter)

            return 1

        case 'SVD':

            print("SONO IN SVD")

            image = np.array(matrixObjFeatures)

            u, s, vt = randomized_svd(image, n_components=2)

            print("\nNumero righe di U: ", len(u))
            print("\nNumero colonne di U: ", len(u[0]))

            matrixS = np.diag(s)
            print("\nNumero righe di S: ", len(matrixS))
            print("\nNumero colonne di S: ", len(matrixS[0]))

            print("\nNumero righe di VT: ", len(vt))
            print("\nNumero colonne di VT: ", len(vt[0]))

            print("\nLeft Singular Vectors:")
            print(u)
            print("\nSingular Values:")
            print(np.diag(s))
            print("\nRight Singular Vectors:")
            print(vt)

            # SVD
            # U, s, VT = svd(image, full_matrices=False) # full_matrices=False
            # print("STAMPO U che ha lunghezza: ", len(U))

            # print("STAMPO U dove un oggetto ha lunghezza: ", len(U[0]))
            # print(U)

            # print("STAMPO S dove un oggetto ha lunghezza: ", len(s))
            # print(s)

            # print("STAMPO V trasposta dove un oggetto ha lunghezza: ", len(VT[0]))
            # print(VT)

            # print("STAMPO A")

            # Traspongo la matrice U per poter iterare sulle righe e quindi costruire la sequenza di coppie soggetto-peso per ogni feature latente

            createDictionaryAndWriteOnFile(u, filtered_dir_list, passedParameter)

            return 2

        case 'LDA':

            # define transform
            lda = LinearDiscriminantAnalysis()
            # prepare transform on dataset
            lda.fit(matrixObjFeatures)
            # apply transform to dataset
            transformed = lda.transform(matrixObjFeatures)

            print("transformed")
            print(transformed)

            # # define the pipeline
            # steps = [('lda', LinearDiscriminantAnalysis()), ('m', GaussianNB())]

            # # It can also be a good idea to standardize data prior to performing the LDA transform if the input variables have differing units or scales; for example:
            # #steps = [('s', StandardScaler()), ('lda', LinearDiscriminantAnalysis()), ('m', GaussianNB())]
            # model = Pipeline(steps=steps)
            return 3

        case _:
            return 4


## Implementazione PCA
https://scikit-learn.org/stable/modules/generated/sklearn.decomposition.PCA.html

In [76]:
ottieniKSemanticheLatenti('LBP', 'cc', 30, 'PCA', 'X')

Numero di file su cui applichiamo i metodi:  399
SONO IN LBP
Lunghezza di un descrittore:  256
SONO IN PCA

Numero righe matrice di covarianza:  256
Numero colonne matrice di covarianza:  256
La matrice di covarianza è quadrata?  True


[[-0.01395663 -0.01645452  0.00249075 ...  0.00171042 -0.00199487
   0.00236129]
 [ 0.00596111 -0.00249595  0.00872789 ...  0.00052361 -0.00112587
  -0.00147431]
 [-0.02533683 -0.01034292  0.00853319 ...  0.00051231 -0.00119992
  -0.00051148]
 ...
 [ 0.00856557 -0.01268216 -0.00459706 ...  0.00126567  0.00274062
  -0.00043185]
 [ 0.00515834 -0.02291602 -0.00615559 ... -0.00163607 -0.00103485
   0.00072398]
 [ 0.01541427 -0.02351884 -0.0041815  ... -0.00086439 -0.00087666
   0.000565  ]]

Numero righe matrice di converted_data:  399
Numero colonne matrice di converted_data:  30


1

In [75]:
ottieniKSemanticheLatenti('LBP', '1', 30, 'PCA', 'Y')

Numero di file su cui applichiamo i metodi:  108
SONO IN LBP
Lunghezza di un descrittore:  256
SONO IN PCA

Numero righe matrice di covarianza:  256
Numero colonne matrice di covarianza:  256
La matrice di covarianza è quadrata?  True


[[-1.48052059e-01 -2.49199518e-03  9.29458306e-02 ...  2.06344040e-04
   2.50872157e-03  1.50483381e-03]
 [-1.25614721e-01 -2.32593198e-03  9.64986598e-02 ...  2.99608752e-03
   2.85026335e-05  7.79877351e-04]
 [-1.47292035e-01  4.60943932e-03  9.63027024e-02 ... -1.03526101e-03
   2.34238025e-03 -1.62534425e-04]
 ...
 [ 3.85464667e-01  7.25733229e-03  2.27383158e-02 ... -1.64821025e-03
   1.40807633e-03 -9.57137635e-05]
 [ 3.91142815e-01  4.17065854e-03  1.35756316e-02 ... -4.91296527e-04
  -8.93258640e-04 -5.44909146e-05]
 [ 3.93687615e-01  2.88669844e-03  1.37047765e-02 ... -2.28252941e-03
  -6.11958991e-05 -6.46731496e-04]]

Numero righe matrice di converted_data:  108
Numero colonne matrice di converted_data:  30


1

## Implementazione SVD
https://machinelearningmastery.com/singular-value-decomposition-for-machine-learning/

In [ ]:
ottieniKSemanticheLatenti('ColorMoments', 'cc', 30, 'SVD', 'X')

In [43]:
ottieniKSemanticheLatenti('ColorMoments', '1', 30, 'SVD', 'Y')

Numero di file su cui applichiamo i metodi:  108
['image-cc-1-1.png', 'image-cc-1-2.png', 'image-cc-1-3.png', 'image-cc-1-4.png', 'image-cc-1-5.png', 'image-cc-1-6.png', 'image-cc-1-7.png', 'image-cc-1-8.png', 'image-cc-1-9.png', 'image-con-1-1.png', 'image-con-1-2.png', 'image-con-1-3.png', 'image-con-1-4.png', 'image-con-1-5.png', 'image-con-1-6.png', 'image-con-1-7.png', 'image-con-1-8.png', 'image-con-1-9.png', 'image-emboss-1-1.png', 'image-emboss-1-2.png', 'image-emboss-1-3.png', 'image-emboss-1-4.png', 'image-emboss-1-5.png', 'image-emboss-1-6.png', 'image-emboss-1-7.png', 'image-emboss-1-8.png', 'image-emboss-1-9.png', 'image-jitter-1-1.png', 'image-jitter-1-2.png', 'image-jitter-1-3.png', 'image-jitter-1-4.png', 'image-jitter-1-5.png', 'image-jitter-1-6.png', 'image-jitter-1-7.png', 'image-jitter-1-8.png', 'image-jitter-1-9.png', 'image-neg-1-1.png', 'image-neg-1-2.png', 'image-neg-1-3.png', 'image-neg-1-4.png', 'image-neg-1-5.png', 'image-neg-1-6.png', 'image-neg-1-7.png', 'i

2

# Implementazione LDA

https://machinelearningmastery.com/linear-discriminant-analysis-for-dimensionality-reduction-in-python/

https://scikit-learn.org/0.16/modules/generated/sklearn.lda.LDA.html

In [13]:
#ottieniKSemanticheLatenti('ColorMoments', 'cc', 3, 'LDA', 'X')

In [14]:
ottieniKSemanticheLatenti('ColorMoments', '14', 3, 'PCA', 'Y')

SONO IN COLOR MOMENTS
ottieniDescrittoreSecondaParte
image-cc-14-1.png
1
Sono in split
r:  64 , h: 64
prima del return
2
Numero di sottoimmagini:  64
Lunghezza array delle medie:  64
indice i  0
[[198 207 255 255 255 255 232 240]
 [245 248 255 255 255 255 237 238]
 [255 255 255 251 255 238 231 233]
 [255 255 255 255 245 224 227 231]
 [255 255 255 255 246 226 240 233]
 [255 242 255 255 242 223 244 223]
 [255 239 255 255 242 217 226 219]
 [255 251 255 255 254 211 201 246]]
[-2.14145119 -1.68143761  0.         -2.26778684 -0.135569    0.51648289
 -1.29965681 -0.19754029]
-1.195917627387833
indice i  1
[[255 237 229 251 255 255 255 255]
 [250 229 236 255 255 250 240 247]
 [239 225 245 255 240 235 234 243]
 [230 222 236 246 245 250 250 250]
 [208 201 229 255 255 255 243 229]
 [185 219 255 255 255 249 215 203]
 [228 255 255 255 253 210 198 192]
 [255 255 255 226 193 173 215 248]]
[-0.79826087  0.06433392  0.04078421 -1.87252344 -1.97627119 -1.37945975
 -0.446652   -0.90564773]
-1.22086314162

1

# Domande

> **Domanda 1:** "ciasuna feature latente deve essere espressa come una sequenza di coppie soggetto-peso". Cosa intendiamo con "peso"? Il contriuto che quella feature latente dà a quel soggetto? (Quindi dobbiamo leggere la maatrice U che descrive gli oggetti rispetto alle feature latenti). Oppure si intende il peso associato alla feature latente per poter ricostruire il db di partenza?